In [1]:
import cnvpytor
import subprocess

print(cnvpytor.__version__)

1.3.1


In [2]:
filename = "test_with_del__1_formated.fa"
command = f"cat {filename} | wc -l"
result = subprocess.check_output(command, shell=True)
line_count = int(result.strip())
line_count

3070445

In [3]:
read_count = line_count * 50 * 30 / 202
read_count = round(read_count)
read_count

22800334

In [4]:
command = f"wgsim -d 300 -N {read_count} -1 101 -2 101 {filename} frag1Copy_test.fastq frag2Copy_test.fastq"
result = subprocess.check_output(command, shell=True)
print(result)

[wgsim] seed = 1707151423
[wgsim_core] calculating the total length of the reference sequence...
[wgsim_core] 1 sequences, total length: 153522198


b'chr22\t3\tA\tR\t+\nchr22\t655\tT\tY\t+\nchr22\t1496\tG\tK\t+\nchr22\t1574\tA\tG\t-\nchr22\t1798\tA\tG\t-\nchr22\t3190\tG\tC\t-\nchr22\t4288\tT\tY\t+\nchr22\t4882\t-\tA\t+\nchr22\t5233\tT\tK\t+\nchr22\t6205\tTT\t-\t-\nchr22\t7798\tA\tR\t+\nchr22\t8321\tG\tS\t+\nchr22\t9306\tA\tW\t+\nchr22\t10352\tA\tT\t-\nchr22\t10930\tT\tG\t-\nchr22\t11052\tC\tA\t-\nchr22\t11549\tT\tC\t-\nchr22\t13011\tA\tW\t+\nchr22\t13905\tA\tT\t-\nchr22\t14002\tG\tA\t-\nchr22\t14244\tT\tY\t+\nchr22\t16405\tG\tR\t+\nchr22\t16630\tC\tY\t+\nchr22\t16731\tC\tY\t+\nchr22\t18125\tA\tR\t+\nchr22\t19136\tG\tS\t+\nchr22\t19742\tA\tR\t+\nchr22\t19919\tA\tM\t+\nchr22\t20739\tA\tM\t+\nchr22\t23925\tA\tM\t+\nchr22\t25425\tT\t-\t-\nchr22\t25748\tC\tM\t+\nchr22\t25843\tT\tK\t+\nchr22\t26394\t-\tG\t+\nchr22\t29131\tA\tR\t+\nchr22\t33063\tT\tG\t-\nchr22\t34186\tTT\t-\t-\nchr22\t35005\tC\tY\t+\nchr22\t35029\tA\tM\t+\nchr22\t35317\tT\tK\t+\nchr22\t35911\tG\tT\t-\nchr22\t37071\tT\tY\t+\nchr22\t38094\tA\tR\t+\nchr22\t38744\tA\tM\t+\nc

In [5]:
# bowtie related stuff
!bowtie2-build reference.fa bias
!bowtie2 -p 4 -k 15 --no-mixed -x bias -1 frag1Copy_test.fastq -2 frag2Copy_test.fastq -S biasOut.sam

Settings:
  Output files: "bias.*.bt2"
  Line rate: 6 (line is 64 bytes)
  Lines per side: 1 (side is 64 bytes)
  Offset rate: 4 (one in 16)
  FTable chars: 10
  Strings: unpacked
  Max bucket size: default
  Max bucket size, sqrt multiplier: default
  Max bucket size, len divisor: 4
  Difference-cover sample period: 1024
  Endianness: little
  Actual local endianness: little
  Sanity checking: disabled
  Assertions: disabled
  Random seed: 0
  Sizeofs: void*:8, int:4, long:8, size_t:8
Input files DNA, FASTA:
  reference.fa
Building a SMALL index
Reading reference sizes
  Time reading reference sizes: 00:00:00
Calculating joined length
Writing header
Reserving space for joined string
Joining reference sequences
  Time to join reference sequences: 00:00:01
bmax according to bmaxDivN setting: 12826141
Using parameters --bmax 9619606 --dcv 1024
  Doing ahead-of-time memory usage test
  Passed!  Constructing with these parameters: --bmax 9619606 --dcv 1024
Constructing suffix-array element

In [6]:
# sam to bam file conversion
!samtools sort biasOut.sam -o biasOut_sorted.bam
!samtools index biasOut_sorted.bam

[bam_sort_core] merging from 27 files and 1 in-memory blocks...


In [7]:
app = cnvpytor.Root("test.pytor", create=True, max_cores=8)

In [8]:
app.rd(["biasOut_sorted.bam"])

In [9]:
app.calculate_histograms([100, 1000, 10000, 100000, 1000000, 10000000])

In [10]:
app.partition([100, 1000, 10000, 100000, 1000000, 10000000])

In [11]:
calls = app.call([100, 1000, 10000, 100000, 1000000, 10000000], print_calls=True)

duplication	chr22:643201-644800	1600	1.3895	6.594815e-05	8.503171e-05	1.000000e+00	1.000000e+00	0.0000	1.0000	0
duplication	chr22:1306401-1325100	18700	1.3071	0.000000e+00	1.315802e-75	0.000000e+00	1.378439e-66	0.0000	1.0000	0
duplication	chr22:2926301-2963000	36700	2.9330	0.000000e+00	0.000000e+00	0.000000e+00	0.000000e+00	0.0000	1.0000	0
duplication	chr22:4546401-4713300	166900	1.5580	0.000000e+00	0.000000e+00	0.000000e+00	0.000000e+00	0.0000	1.0000	0
duplication	chr22:6655101-6661800	6700	2.2826	0.000000e+00	1.732980e-149	0.000000e+00	1.255410e-181	0.0000	1.0000	0
duplication	chr22:6848401-6854600	6200	1.5681	0.000000e+00	1.084627e-43	0.000000e+00	8.938677e-49	0.0000	1.0000	0
duplication	chr22:8039401-8047800	8400	1.8247	0.000000e+00	7.513016e-104	0.000000e+00	3.648878e-117	0.0000	1.0000	0
duplication	chr22:9424201-9461600	37400	1.3912	0.000000e+00	2.835232e-215	0.000000e+00	2.700781e-203	0.0000	1.0000	0
duplication	chr22:13230601-13395900	165300	1.3163	0.000000e+00	0.000000e+00	0.0

In [12]:
for bin_size in calls:
    print("Bin size: ", bin_size)

Bin size:  100
Bin size:  1000
Bin size:  10000
Bin size:  100000
Bin size:  1000000
Bin size:  10000000


In [13]:
print(f"{filename=}, Histogram Size: 100")
print("type,chromosome_name,start,end,size,cnv_level,q0")

for call in calls[100]:
    print(call[0], call[1], call[2], call[3], call[4], call[5], call[10], sep=",")

filename='test_with_del__1_formated.fa', Histogram Size: 100
type,chromosome_name,start,end,size,cnv_level,q0
duplication,chr22,643201,644800,1600,1.3894675353584531,0.0
duplication,chr22,1306401,1325100,18700,1.307145465989671,0.0
duplication,chr22,2926301,2963000,36700,2.932968424141799,0.0
duplication,chr22,4546401,4713300,166900,1.5580377037443522,0.0
duplication,chr22,6655101,6661800,6700,2.28264275278437,0.0
duplication,chr22,6848401,6854600,6200,1.56807674062001,0.0
duplication,chr22,8039401,8047800,8400,1.8246764391638275,0.0
duplication,chr22,9424201,9461600,37400,1.3912317505258236,0.0
duplication,chr22,13230601,13395900,165300,1.3162506733441584,0.0
duplication,chr22,13480901,13512800,31900,3.9632685525111295,0.0
duplication,chr22,15242601,15246200,3600,2.882215345827317,0.0
duplication,chr22,18704901,18881400,176500,2.111117945754201,0.00016271879867035496
deletion,chr22,18881401,19258600,377200,0.7376960190484133,0.0001015491394814224
duplication,chr22,19258601,19268300,97

In [14]:
print(f"{filename=}, Histogram Size: 1000")
print("type,chromosome_name,start,end,size,cnv_level,q0")

for call in calls[1000]:
    print(call[0], call[1], call[2], call[3], call[4], call[5], call[10], sep=",")

filename='test_with_del__1_formated.fa', Histogram Size: 1000
type,chromosome_name,start,end,size,cnv_level,q0
duplication,chr22,1306001,1325000,19000,1.3080818488707817,0.0
duplication,chr22,2926001,2963000,37000,2.9239507292318314,0.0
duplication,chr22,4546001,4713000,167000,1.5594727165235818,0.0
duplication,chr22,6655001,6662000,7000,2.2414645476134747,0.0
duplication,chr22,8040001,8048000,8000,1.824310089413542,0.0
duplication,chr22,13231001,13396000,165000,1.3179017822457222,0.0
duplication,chr22,13481001,13513000,32000,3.9574172851791616,0.0
duplication,chr22,18711001,18881000,170000,2.141866312618752,0.00014381878832670834
deletion,chr22,18883001,19259000,376000,0.7373823967998885,0.00010171252943582713
duplication,chr22,19259001,19268000,9000,2.463822516207555,0.0
deletion,chr22,20673001,21248000,575000,0.7449002316586227,0.0003226594028407432
deletion,chr22,21624001,23607000,1983000,0.7475856375658633,0.00017330986601654736
duplication,chr22,23608001,23613000,5000,1.656122352

In [15]:
print(f"{filename=}, Histogram Size: 10,000")
print("type,chromosome_name,start,end,size,cnv_level,q0")

for call in calls[10000]:
    print(call[0], call[1], call[2], call[3], call[4], call[5], call[10], sep=",")

filename='test_with_del__1_formated.fa', Histogram Size: 10,000
type,chromosome_name,start,end,size,cnv_level,q0
duplication,chr22,4550001,4710000,160000,1.5582932626462855,0.0
duplication,chr22,18710001,18880000,170000,2.1309540025691898,0.0001477644611579923
deletion,chr22,18880001,19170000,290000,0.7464959645820359,0.00011553194410905458
duplication,chr22,19170001,19510000,340000,0.7891712349157158,8.594196615267744e-05
duplication,chr22,28470001,28600000,130000,2.297750292845387,4.550236681250405e-05
duplication,chr22,30800001,30980000,180000,2.7413230743387813,2.7198751165219225e-05
duplication,chr22,31150001,31360000,210000,1.5799468052674492,4.067433110754355e-05
duplication,chr22,35940001,36200000,260000,2.184942843738122,4.286591324375084e-05
duplication,chr22,43500001,50360000,6860000,1.7771905216351715,7.299515539013671e-05
duplication,chr22,50420001,51310000,890000,2.031884935864168,0.00016277073204499677


In [16]:
print(f"{filename=}, Histogram Size: 100,000")
print("type,chromosome_name,start,end,size,cnv_level,q0")

for call in calls[100000]:
    print(call[0], call[1], call[2], call[3], call[4], call[5], call[10], sep=",")

filename='test_with_del__1_formated.fa', Histogram Size: 100,000
type,chromosome_name,start,end,size,cnv_level,q0
duplication,chr22,30800001,36200000,5400000,1.332254713728896,6.798390531524759e-05
duplication,chr22,44100001,51400000,7300000,1.8134886021478667,7.64599418681382e-05


In [17]:
print(f"{filename=}, Histogram Size: 1,000,000")
print("type,chromosome_name,start,end,size,cnv_level,q0")

for call in calls[1000000]:
    print(call[0], call[1], call[2], call[3], call[4], call[5], call[10], sep=",")

filename='test_with_del__1_formated.fa', Histogram Size: 1,000,000
type,chromosome_name,start,end,size,cnv_level,q0
duplication,chr22,42000001,51000000,9000000,1.7313368316674824,8.758944214292244e-05


In [18]:
print(f"{filename=}, Histogram Size: 10,000,000")
print("type,chromosome_name,start,end,size,cnv_level,q0")

for call in calls[10000000]:
    print(call[0], call[1], call[2], call[3], call[4], call[5], call[10], sep=",")

filename='test_with_del__1_formated.fa', Histogram Size: 10,000,000
type,chromosome_name,start,end,size,cnv_level,q0


In [19]:
del app